In [1]:
import requests_cache
import requests
import pandas as pd
from matplotlib import pyplot as plt
plt.style.use('ggplot')
%matplotlib inline
from pandas.tools.plotting import scatter_matrix
import numpy as np
import seaborn as sns
from requests_oauthlib import OAuth1Session
from bs4 import BeautifulSoup


In [2]:
requests_cache.install_cache("cache")

def yelp_search(term, location):
    """
    makes a search request
    
    Argument: search term, location
    
    Return: search result items as a list (for 0 items, return an empty list)
    """
    consumer_key = "uFKYftN0fu4pD6guW2cYng"
    consumer_secret = "iUYQ2Hk3-vTQVd0zOFnvloWPivA"
    token = "FZnep4FiFmwrrifuNm6M-_K661Wb3J02"
    token_secret = "CRvBo_fO-r4pE_-p2UrnN_mxBlc"
   
    urlbase = "http://api.yelp.com/v2/search"
    params = ({"term": term})
    # 2=Highest Rated 
    params.update({"location": location, "sort": "2", "cll" : "latitude,longitude"})
    session = OAuth1Session(consumer_key, consumer_secret,token,token_secret)
     
    request = session.get(urlbase,params=params)
   
    #Transforms JSON API response into dictionary
    data = request.json()
    session.close()
    output = data
    
    if "businesses" not in output:
        return {}
    
    else:
        return output["businesses"]


In [6]:
data = yelp_search("hotels", "94123")

[{u'categories': [[u'Hotels', u'hotels'],
   [u'Bed & Breakfast', u'bedbreakfast']],
  u'display_phone': u'+1-415-776-5462',
  u'id': u'chateau-tivoli-bed-and-breakfast-inn-san-francisco',
  u'image_url': u'https://s3-media3.fl.yelpcdn.com/bphoto/5I0fNewKq-Bb736BxVy8aQ/ms.jpg',
  u'is_claimed': True,
  u'is_closed': False,
  u'location': {u'address': [u'1057 Steiner St'],
   u'city': u'San Francisco',
   u'coordinate': {u'latitude': 37.7791, u'longitude': -122.43368},
   u'country_code': u'US',
   u'cross_streets': u'Golden Gate Ave & Mcallister St',
   u'display_address': [u'1057 Steiner St',
    u'Alamo Square',
    u'San Francisco, CA 94115'],
   u'geo_accuracy': 8.0,
   u'neighborhoods': [u'Alamo Square'],
   u'postal_code': u'94115',
   u'state_code': u'CA'},
  u'mobile_url': u'https://m.yelp.com/biz/chateau-tivoli-bed-and-breakfast-inn-san-francisco?adjust_creative=uFKYftN0fu4pD6guW2cYng&utm_campaign=yelp_api&utm_medium=api_v2_search&utm_source=uFKYftN0fu4pD6guW2cYng',
  u'name':

In [4]:
df = pd.DataFrame(data)

In [5]:
url = "https://en.wikipedia.org/wiki/List_of_cities_and_towns_in_California"
content = requests.get(url).content
wikisoup = BeautifulSoup(content, 'lxml')
city_data = wikisoup.findAll("th", {"scope": "row"})

In [8]:
emptylist = []
city_list = [emptylist.append(city.text) for city in city_data]
city_df = pd.DataFrame(emptylist)
city_df = city_df[1:483]

In [9]:
city_df = city_df.rename(columns={0: "city"})

In [10]:
def search(city):
    result = yelp_search("hotels", city)
    df_result = pd.DataFrame(result)
    df_result["city"] = city
    return df_result

In [11]:
yelp = [search(city) for city in city_df["city"]]

In [12]:
yelp_df = [pd.DataFrame(data) for data in yelp]

In [14]:
yelp_df

[                                           categories    display_phone  \
 0   [[Limos, limos], [Party Bus Rentals, partybusr...  +1-888-546-6112   
 1                           [[Rest Stops, reststops]]              NaN   
 2                             [[RV Rental, rvrental]]  +1-760-662-7676   
 3   [[Tours, tours], [Motorcycle Rental, motorcycl...  +1-760-249-1105   
 4                                  [[Hotels, hotels]]  +1-888-293-5571   
 5   [[Limos, limos], [Party Bus Rentals, partybusr...  +1-760-843-0234   
 6   [[Hotels, hotels], [American (Traditional), tr...  +1-760-952-1200   
 7                                  [[Hotels, hotels]]  +1-760-949-9900   
 8                                  [[Hotels, hotels]]  +1-760-949-1515   
 9              [[Airport Shuttles, airport_shuttles]]  +1-760-486-8821   
 10                                 [[Hotels, hotels]]  +1-760-244-8254   
 11  [[Hotels, hotels], [Venues & Event Spaces, ven...  +1-760-244-7674   
 12                      